# Trexquant Interview Project (The Hangman Game)

* Copyright Trexquant Investment LP. All Rights Reserved. 
* Redistribution of this question without written consent from Trexquant is prohibited

## Instruction:
For this coding test, your mission is to write an algorithm that plays the game of Hangman through our API server. 

When a user plays Hangman, the server first selects a secret word at random from a list. The server then returns a row of underscores (space separated)—one for each letter in the secret word—and asks the user to guess a letter. If the user guesses a letter that is in the word, the word is redisplayed with all instances of that letter shown in the correct positions, along with any letters correctly guessed on previous turns. If the letter does not appear in the word, the user is charged with an incorrect guess. The user keeps guessing letters until either (1) the user has correctly guessed all the letters in the word
or (2) the user has made six incorrect guesses.

You are required to write a "guess" function that takes current word (with underscores) as input and returns a guess letter. You will use the API codes below to play 1,000 Hangman games. You have the opportunity to practice before you want to start recording your game results.

Your algorithm is permitted to use a training set of approximately 250,000 dictionary words. Your algorithm will be tested on an entirely disjoint set of 250,000 dictionary words. Please note that this means the words that you will ultimately be tested on do NOT appear in the dictionary that you are given. You are not permitted to use any dictionary other than the training dictionary we provided. This requirement will be strictly enforced by code review.

You are provided with a basic, working algorithm. This algorithm will match the provided masked string (e.g. a _ _ l e) to all possible words in the dictionary, tabulate the frequency of letters appearing in these possible words, and then guess the letter with the highest frequency of appearence that has not already been guessed. If there are no remaining words that match then it will default back to the character frequency distribution of the entire dictionary.

This benchmark strategy is successful approximately 18% of the time. Your task is to design an algorithm that significantly outperforms this benchmark.

In [1]:
import json
import requests
import random
import string
import secrets
import time
import re
import collections
import torch
try:
    from urllib.parse import parse_qs, urlencode, urlparse
except ImportError:
    from urlparse import parse_qs, urlparse
    from urllib import urlencode

from requests.packages.urllib3.exceptions import InsecureRequestWarning

requests.packages.urllib3.disable_warnings(InsecureRequestWarning)

I have trained the same model in different ways named m1 to m10.
The model architecture is also given in the class.
The particular model can be changed in the init of HangmanAPI class.

In [16]:
class HangmanAPI(object):
    def __init__(self, access_token=None, session=None, timeout=None):
        self.hangman_url = self.determine_hangman_url()
        self.access_token = access_token
        self.session = session or requests.Session()
        self.timeout = timeout
        self.guessed_letters = []
        
        full_dictionary_location = "words_250000_train.txt"
        self.full_dictionary = self.build_dictionary(full_dictionary_location)        
        self.full_dictionary_common_letter_sorted = collections.Counter("".join(self.full_dictionary)).most_common()
        
        self.current_dictionary = []
        self.device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        self.model = None
        self._tok = self._CharTokenizer()
        self._maybe_load_model("m9.pt")   # change path/filename if needed

        
    @staticmethod
    def determine_hangman_url():
        links = ['https://trexsim.com']

        data = {link: 0 for link in links}

        for link in links:

            requests.get(link)

            for i in range(10):
                s = time.time()
                requests.get(link)
                data[link] = time.time() - s

        link = sorted(data.items(), key=lambda x: x[1])[0][0]
        link += '/trexsim/hangman'
        return link

    # --- add these helpers as methods of HangmanAPI ---
    class _CharTokenizer:
        # [PAD]=0, [MASK]=1, [CLS]=2, 'a'..'z'->3..28
        def __init__(self):
            self.pad_id  = 0
            self.mask_id = 1
            self.cls_id  = 2
            self.letter2id = {chr(i): 3 + (i-97) for i in range(97, 123)}
    
        def encode_board(self, pattern: str):
            return [self.mask_id if ch == "_" else self.letter2id[ch] for ch in pattern]
    
        def with_cls(self, ids):
            return [self.cls_id] + ids
    
    def _maybe_load_model(self, path: str):
        try:
            import torch, torch.nn as nn
            ckpt = torch.load(path, map_location="cpu")
    
            # minimal model shell matching your trained architecture
            class TinyCharTransformer(nn.Module):
                def __init__(self, vocab_size=29, d_model=256, n_heads=8, n_layers=4,
                             d_ff=512, max_len=32):
                    super().__init__()
                    self.token_emb = nn.Embedding(vocab_size, d_model)
                    self.pos_emb   = nn.Embedding(max_len, d_model)
                    enc = nn.TransformerEncoderLayer(
                        d_model=d_model,
                        nhead=n_heads,
                        dim_feedforward=d_ff,
                        batch_first=True
                    )
                    self.encoder = nn.TransformerEncoder(enc, num_layers=n_layers)
                    self.cls_head = nn.Linear(d_model, 26)
                    self.max_len = max_len
    
                def forward(self, token_ids):
                    B, T = token_ids.size()
                    if T > self.max_len:
                        raise ValueError(f"seq len {T} > max_len {self.max_len}")
                    pos = torch.arange(T, device=token_ids.device).unsqueeze(0).expand(B, T)
                    x = self.token_emb(token_ids) + self.pos_emb(pos)
                    x = self.encoder(x)
                    cls = x[:, 0, :]
                    return self.cls_head(cls)
    
            # construct using ckpt config if present; else use defaults above
            if isinstance(ckpt, dict) and "state_dict" in ckpt:
                cfg = ckpt.get("config", {})
                # fill from cfg when available; otherwise keep our new defaults
                self.model = TinyCharTransformer(
                    vocab_size=cfg.get("vocab_size", 29),
                    d_model=cfg.get("d_model", 256),
                    n_heads=cfg.get("n_heads", 8),
                    n_layers=cfg.get("n_layers", 4),
                    d_ff=cfg.get("d_ff", 512),
                    max_len=cfg.get("max_len", 32),
                )
                self.model.load_state_dict(ckpt["state_dict"], strict=False)
            else:
                # raw state_dict with no config: assume your new defaults
                self.model = TinyCharTransformer()
                self.model.load_state_dict(ckpt, strict=False)
    
            self.model.eval().to(self.device)
        except Exception as e:
            print(f"[warn] could not load model from {path}: {e}")
            self.model = None

    def guess(self, word):  # word example: "_ p p _ e "
        # parse board → pattern without spaces
        pattern = word[::2]                    # "_pp_e"
        present = set(ch for ch in pattern if ch != "_")
        already = set(self.guessed_letters)    # what we've guessed so far
    
        # if we have a model, use it
        if self.model is not None:
            # build input ids: [CLS] + encoded pattern
            ids = self._tok.with_cls(self._tok.encode_board(pattern))
            x = torch.tensor(ids, dtype=torch.long, device=self.device).unsqueeze(0)  # [1, T]
            with torch.no_grad():
                logits = self.model(x)[0]      # [26]
                probs = torch.softmax(logits, dim=-1).cpu().numpy()
    
            # rank letters by prob (highest first)
            import numpy as np, string
            letters = list(string.ascii_lowercase)
            order = np.argsort(-probs)         # indices 0..25
    
            # pick first letter that we haven't already guessed and isn't already on board
            for idx in order:
                cand = letters[idx]
                if cand not in already and cand not in present:
                    return cand
    
        # fallback: simple static prior if no model choice available
        # (etaoin… minus already-guessed and present)
        for cand in "etaoinshrdlucmfwypvbgkjqxz":
            if cand not in already and cand not in present:
                return cand
    
        # ultimate fallback (everything guessed?): pick any letter not in already
        import string
        for cand in string.ascii_lowercase:
            if cand not in already:
                return cand
        return "e"  # last resort

    ##########################################################
    # You'll likely not need to modify any of the code below #
    ##########################################################
    
    def build_dictionary(self, dictionary_file_location):
        text_file = open(dictionary_file_location,"r")
        full_dictionary = text_file.read().splitlines()
        text_file.close()
        return full_dictionary
                
    def start_game(self, practice=True, verbose=True):
        # reset guessed letters to empty set and current plausible dictionary to the full dictionary
        self.guessed_letters = []
        self.current_dictionary = self.full_dictionary
                         
        response = self.request("/new_game", {"practice":practice})
        if response.get('status')=="approved":
            game_id = response.get('game_id')
            word = response.get('word')
            tries_remains = response.get('tries_remains')
            if verbose:
                print("Successfully start a new game! Game ID: {0}. # of tries remaining: {1}. Word: {2}.".format(game_id, tries_remains, word))
            while tries_remains>0:
                # get guessed letter from user code
                guess_letter = self.guess(word)
                    
                # append guessed letter to guessed letters field in hangman object
                self.guessed_letters.append(guess_letter)
                if verbose:
                    print("Guessing letter: {0}".format(guess_letter))
                    
                try:    
                    res = self.request("/guess_letter", {"request":"guess_letter", "game_id":game_id, "letter":guess_letter})
                except HangmanAPIError:
                    print('HangmanAPIError exception caught on request.')
                    continue
                except Exception as e:
                    print('Other exception caught on request.')
                    raise e
               
                if verbose:
                    print("Sever response: {0}".format(res))
                status = res.get('status')
                tries_remains = res.get('tries_remains')
                if status=="success":
                    if verbose:
                        print("Successfully finished game: {0}".format(game_id))
                    return True
                elif status=="failed":
                    reason = res.get('reason', '# of tries exceeded!')
                    if verbose:
                        print("Failed game: {0}. Because of: {1}".format(game_id, reason))
                    return False
                elif status=="ongoing":
                    word = res.get('word')
        else:
            if verbose:
                print("Failed to start a new game")
        return status=="success"
        
    def my_status(self):
        return self.request("/my_status", {})
    
    def request(
            self, path, args=None, post_args=None, method=None):
        if args is None:
            args = dict()
        if post_args is not None:
            method = "POST"

        # Add `access_token` to post_args or args if it has not already been
        # included.
        if self.access_token:
            # If post_args exists, we assume that args either does not exists
            # or it does not need `access_token`.
            if post_args and "access_token" not in post_args:
                post_args["access_token"] = self.access_token
            elif "access_token" not in args:
                args["access_token"] = self.access_token

        time.sleep(0.2)

        num_retry, time_sleep = 50, 2
        for it in range(num_retry):
            try:
                response = self.session.request(
                    method or "GET",
                    self.hangman_url + path,
                    timeout=self.timeout,
                    params=args,
                    data=post_args,
                    verify=False
                )
                break
            except requests.HTTPError as e:
                response = json.loads(e.read())
                raise HangmanAPIError(response)
            except requests.exceptions.SSLError as e:
                if it + 1 == num_retry:
                    raise
                time.sleep(time_sleep)

        headers = response.headers
        if 'json' in headers['content-type']:
            result = response.json()
        elif "access_token" in parse_qs(response.text):
            query_str = parse_qs(response.text)
            if "access_token" in query_str:
                result = {"access_token": query_str["access_token"][0]}
                if "expires" in query_str:
                    result["expires"] = query_str["expires"][0]
            else:
                raise HangmanAPIError(response.json())
        else:
            raise HangmanAPIError('Maintype was not text, or querystring')

        if result and isinstance(result, dict) and result.get("error"):
            raise HangmanAPIError(result)
        return result
    
class HangmanAPIError(Exception):
    def __init__(self, result):
        self.result = result
        self.code = None
        try:
            self.type = result["error_code"]
        except (KeyError, TypeError):
            self.type = ""

        try:
            self.message = result["error_description"]
        except (KeyError, TypeError):
            try:
                self.message = result["error"]["message"]
                self.code = result["error"].get("code")
                if not self.type:
                    self.type = result["error"].get("type", "")
            except (KeyError, TypeError):
                try:
                    self.message = result["error_msg"]
                except (KeyError, TypeError):
                    self.message = result

        Exception.__init__(self, self.message)

# API Usage Examples

## To start a new game:
1. Make sure you have implemented your own "guess" method.
2. Use the access_token that we sent you to create your HangmanAPI object. 
3. Start a game by calling "start_game" method.
4. If you wish to test your function without being recorded, set "practice" parameter to 1.
5. Note: You have a rate limit of 20 new games per minute. DO NOT start more than 20 new games within one minute.

In [17]:
api = HangmanAPI(access_token="cb3e708aec0ed4f3e8e7970478635b", timeout=2000)
#cb3e708aec0ed4f3e8e7970478635b, 74dc83bd753fc3574ed90c9a2533e9, c4c97dbd6d5b2bb5057a51ea318a01

## Playing practice games:
You can use the command below to play up to 100,000 practice games.

In [338]:
api.start_game(practice=1,verbose=True)
[total_practice_runs,total_recorded_runs,total_recorded_successes,total_practice_successes] = api.my_status() # Get my game stats: (# of tries, # of wins)
practice_success_rate = total_practice_successes / total_practice_runs
print('run %d practice games out of an allotted 100,000. practice success rate so far = %.3f' % (total_practice_runs, practice_success_rate))


Successfully start a new game! Game ID: 42f4a6f046d2. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': '42f4a6f046d2', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ _ _ _ _ _ '}
Guessing letter: i
Sever response: {'game_id': '42f4a6f046d2', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ i _ i _ _ '}
Guessing letter: n
Sever response: {'game_id': '42f4a6f046d2', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ i _ i _ n '}
Guessing letter: a
Sever response: {'game_id': '42f4a6f046d2', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ a _ _ _ i _ i _ n '}
Guessing letter: o
Sever response: {'game_id': '42f4a6f046d2', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ a _ o _ i _ i o n '}
Guessing letter: t
Sever response: {'game_id': '42f4a6f046d2', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ t _ a t o _ i _ i o n '}
Guessing letter: s
Sever response: {'game_id': '4

In [19]:
[total_practice_runs,total_recorded_runs,total_recorded_successes,total_practice_successes] = api.my_status() # Get my game stats: (# of tries, # of wins)
practice_success_rate = total_practice_successes / total_practice_runs
print('run %d practice games out of an allotted 100,000. practice success rate so far = %.3f' % (total_practice_runs, practice_success_rate))

run 200 practice games out of an allotted 100,000. practice success rate so far = 0.650


In [18]:
#m9
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#%


=== Game 1/100 ===
Successfully start a new game! Game ID: 562163bfb813. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ .
Guessing letter: i
Sever response: {'game_id': '562163bfb813', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ '}
Guessing letter: e
Sever response: {'game_id': '562163bfb813', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ e _ _ _ e _ _ e _ e _ _ e _ _ '}
Guessing letter: n
Sever response: {'game_id': '562163bfb813', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ e _ _ _ e n _ e _ e _ n e _ _ '}
Guessing letter: s
Sever response: {'game_id': '562163bfb813', 'status': 'ongoing', 'tries_remains': 5, 'word': 's e _ _ _ e n _ e _ e _ n e s s '}
Guessing letter: d
Sever response: {'game_id': '562163bfb813', 'status': 'ongoing', 'tries_remains': 5, 'word': 's e _ _ _ e n _ e _ e d n e s s '}
Guessing letter: l
Sever response: {'game_id': '562163bfb813', 'status': 'ongoing', 'tries_remains': 5, 'word': 's e l _ 

In [35]:
#m9
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#70%


=== Game 1/100 ===
Successfully start a new game! Game ID: c565d75a4c1b. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': 'c565d75a4c1b', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ _ '}
Guessing letter: i
Sever response: {'game_id': 'c565d75a4c1b', 'status': 'ongoing', 'tries_remains': 5, 'word': 'i _ _ _ _ i _ _ '}
Guessing letter: n
Sever response: {'game_id': 'c565d75a4c1b', 'status': 'ongoing', 'tries_remains': 5, 'word': 'i n _ _ _ i _ n '}
Guessing letter: o
Sever response: {'game_id': 'c565d75a4c1b', 'status': 'ongoing', 'tries_remains': 5, 'word': 'i n _ _ _ i o n '}
Guessing letter: t
Sever response: {'game_id': 'c565d75a4c1b', 'status': 'ongoing', 'tries_remains': 4, 'word': 'i n _ _ _ i o n '}
Guessing letter: u
Sever response: {'game_id': 'c565d75a4c1b', 'status': 'ongoing', 'tries_remains': 3, 'word': 'i n _ _ _ i o n '}
Guessing letter: s
Sever response: {'game_id': 'c565d75a4c1b', 'status': 'ongoing', '

In [64]:
#m10
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#67%


=== Game 1/100 ===
Successfully start a new game! Game ID: fdc01f920b5a. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': 'fdc01f920b5a', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ _ _ e _ _ '}
Guessing letter: s
Sever response: {'game_id': 'fdc01f920b5a', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ _ _ e _ s '}
Guessing letter: r
Sever response: {'game_id': 'fdc01f920b5a', 'status': 'ongoing', 'tries_remains': 6, 'word': 'r _ _ _ _ e _ s '}
Guessing letter: l
Sever response: {'game_id': 'fdc01f920b5a', 'status': 'ongoing', 'tries_remains': 6, 'word': 'r _ _ _ _ e l s '}
Guessing letter: a
Sever response: {'game_id': 'fdc01f920b5a', 'status': 'ongoing', 'tries_remains': 5, 'word': 'r _ _ _ _ e l s '}
Guessing letter: o
Sever response: {'game_id': 'fdc01f920b5a', 'status': 'ongoing', 'tries_remains': 5, 'word': 'r o _ _ _ e l s '}
Guessing letter: t
Sever response: {'game_id': 'fdc01f920b5a', 'status': 'ongoing', '

In [57]:
#m10
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#66%


=== Game 1/100 ===
Successfully start a new game! Game ID: 3054a234f879. # of tries remaining: 6. Word: _ _ _ _ .
Guessing letter: a
Sever response: {'game_id': '3054a234f879', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ '}
Guessing letter: e
Sever response: {'game_id': '3054a234f879', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ e '}
Guessing letter: i
Sever response: {'game_id': '3054a234f879', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ _ e '}
Guessing letter: o
Sever response: {'game_id': '3054a234f879', 'status': 'ongoing', 'tries_remains': 3, 'word': '_ _ _ e '}
Guessing letter: u
Sever response: {'game_id': '3054a234f879', 'status': 'ongoing', 'tries_remains': 2, 'word': '_ _ _ e '}
Guessing letter: y
Sever response: {'game_id': '3054a234f879', 'status': 'ongoing', 'tries_remains': 2, 'word': '_ y _ e '}
Guessing letter: r
Sever response: {'game_id': '3054a234f879', 'status': 'ongoing', 'tries_remains': 1, 'word': '_ y _ e '}
Guessing letter: 

In [55]:
#m10
N = 1000
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#63.3%


=== Game 1/1000 ===
Successfully start a new game! Game ID: 146996963ea5. # of tries remaining: 6. Word: _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': '146996963ea5', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ e _ _ _ _ '}
Guessing letter: a
Sever response: {'game_id': '146996963ea5', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ e _ _ a _ '}
Guessing letter: r
Sever response: {'game_id': '146996963ea5', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ e _ _ a _ '}
Guessing letter: n
Sever response: {'game_id': '146996963ea5', 'status': 'ongoing', 'tries_remains': 5, 'word': 'n e _ _ a _ '}
Guessing letter: l
Sever response: {'game_id': '146996963ea5', 'status': 'ongoing', 'tries_remains': 4, 'word': 'n e _ _ a _ '}
Guessing letter: t
Sever response: {'game_id': '146996963ea5', 'status': 'ongoing', 'tries_remains': 3, 'word': 'n e _ _ a _ '}
Guessing letter: s
Sever response: {'game_id': '146996963ea5', 'status': 'ongoing', 'tries_remains': 2, 'word': 

In [54]:
#m10
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#62%


=== Game 1/100 ===
Successfully start a new game! Game ID: d42bbc61b963. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ _ _ _ _ _ .
Guessing letter: i
Sever response: {'game_id': 'd42bbc61b963', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i _ _ _ _ _ _ _ _ _ i _ _ '}
Guessing letter: n
Sever response: {'game_id': 'd42bbc61b963', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i _ _ _ _ _ _ _ _ _ i _ n '}
Guessing letter: o
Sever response: {'game_id': 'd42bbc61b963', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i _ _ _ _ _ _ _ _ _ i o n '}
Guessing letter: t
Sever response: {'game_id': 'd42bbc61b963', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i _ _ _ _ _ _ _ _ t i o n '}
Guessing letter: e
Sever response: {'game_id': 'd42bbc61b963', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i _ _ _ _ _ e _ _ t i o n '}
Guessing letter: a
Sever response: {'game_id': 'd42bbc61b963', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i _ a _ _ _ e _ a t i o n '}
G

In [52]:
#m10
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#67%


=== Game 1/100 ===
Successfully start a new game! Game ID: ebf23422dd1b. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': 'ebf23422dd1b', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ _ '}
Guessing letter: a
Sever response: {'game_id': 'ebf23422dd1b', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ a _ _ _ '}
Guessing letter: r
Sever response: {'game_id': 'ebf23422dd1b', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ a r _ _ '}
Guessing letter: s
Sever response: {'game_id': 'ebf23422dd1b', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ a r _ s '}
Guessing letter: d
Sever response: {'game_id': 'ebf23422dd1b', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ d _ a r d s '}
Guessing letter: i
Sever response: {'game_id': 'ebf23422dd1b', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ d _ a r d s '}
Guessing letter: o
Sever response: {'game_id': 'ebf23422dd1b', 'status': 'ongoing', '

In [51]:
#m10
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#64%


=== Game 1/100 ===
Successfully start a new game! Game ID: 53d57ca8d464. # of tries remaining: 6. Word: _ _ _ _ _ .
Guessing letter: a
Sever response: {'game_id': '53d57ca8d464', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ a _ '}
Guessing letter: e
Sever response: {'game_id': '53d57ca8d464', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ a _ '}
Guessing letter: l
Sever response: {'game_id': '53d57ca8d464', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ _ a _ '}
Guessing letter: n
Sever response: {'game_id': '53d57ca8d464', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ n a n '}
Guessing letter: u
Sever response: {'game_id': '53d57ca8d464', 'status': 'ongoing', 'tries_remains': 3, 'word': '_ _ n a n '}
Guessing letter: o
Sever response: {'game_id': '53d57ca8d464', 'status': 'ongoing', 'tries_remains': 3, 'word': '_ o n a n '}
Guessing letter: m
Sever response: {'game_id': '53d57ca8d464', 'status': 'ongoing', 'tries_remains': 2, 'word': '_ o n a n '}
G

In [45]:
#m9
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#66%


=== Game 1/100 ===
Successfully start a new game! Game ID: b08ba1bb092a. # of tries remaining: 6. Word: _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': 'b08ba1bb092a', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ '}
Guessing letter: a
Sever response: {'game_id': 'b08ba1bb092a', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ a _ _ _ '}
Guessing letter: n
Sever response: {'game_id': 'b08ba1bb092a', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ n a _ _ _ '}
Guessing letter: o
Sever response: {'game_id': 'b08ba1bb092a', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ o n a _ _ o '}
Guessing letter: c
Sever response: {'game_id': 'b08ba1bb092a', 'status': 'ongoing', 'tries_remains': 5, 'word': 'c o n a _ _ o '}
Guessing letter: t
Sever response: {'game_id': 'b08ba1bb092a', 'status': 'ongoing', 'tries_remains': 4, 'word': 'c o n a _ _ o '}
Guessing letter: l
Sever response: {'game_id': 'b08ba1bb092a', 'status': 'ongoing', 'tries_remains'

In [34]:
#m9
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#65%


=== Game 1/100 ===
Successfully start a new game! Game ID: 137e8ce33bbc. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ .
Guessing letter: i
Sever response: {'game_id': '137e8ce33bbc', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i _ _ _ _ _ _ i _ _ _ _ _ _ _ '}
Guessing letter: e
Sever response: {'game_id': '137e8ce33bbc', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i _ _ e _ _ _ i _ _ e _ e _ _ '}
Guessing letter: n
Sever response: {'game_id': '137e8ce33bbc', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i _ _ e _ _ _ i _ _ e n e _ _ '}
Guessing letter: s
Sever response: {'game_id': '137e8ce33bbc', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i s _ e _ _ _ i _ _ e n e s s '}
Guessing letter: l
Sever response: {'game_id': '137e8ce33bbc', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i s _ e _ _ _ i _ l e n e s s '}
Guessing letter: b
Sever response: {'game_id': '137e8ce33bbc', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ i s _ 

In [30]:
#m5
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#57%


=== Game 1/100 ===
Successfully start a new game! Game ID: 379745cb3e6d. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': '379745cb3e6d', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ _ _ _ _ e '}
Guessing letter: i
Sever response: {'game_id': '379745cb3e6d', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ e '}
Guessing letter: a
Sever response: {'game_id': '379745cb3e6d', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ a _ a _ _ _ e '}
Guessing letter: r
Sever response: {'game_id': '379745cb3e6d', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ a r a _ _ _ e '}
Guessing letter: p
Sever response: {'game_id': '379745cb3e6d', 'status': 'ongoing', 'tries_remains': 5, 'word': 'p a r a _ _ _ e '}
Guessing letter: n
Sever response: {'game_id': '379745cb3e6d', 'status': 'ongoing', 'tries_remains': 4, 'word': 'p a r a _ _ _ e '}
Guessing letter: t
Sever response: {'game_id': '379745cb3e6d', 'status': 'ongoing', '

In [16]:
#m8
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#55%


=== Game 1/100 ===
Successfully start a new game! Game ID: b309f8eb2de2. # of tries remaining: 6. Word: _ _ _ _ _ .
Guessing letter: a
Sever response: {'game_id': 'b309f8eb2de2', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ a _ a _ '}
Guessing letter: n
Sever response: {'game_id': 'b309f8eb2de2', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ a _ a _ '}
Guessing letter: r
Sever response: {'game_id': 'b309f8eb2de2', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ a _ a _ '}
Guessing letter: l
Sever response: {'game_id': 'b309f8eb2de2', 'status': 'ongoing', 'tries_remains': 3, 'word': '_ a _ a _ '}
Guessing letter: s
Sever response: {'game_id': 'b309f8eb2de2', 'status': 'ongoing', 'tries_remains': 2, 'word': '_ a _ a _ '}
Guessing letter: m
Sever response: {'game_id': 'b309f8eb2de2', 'status': 'ongoing', 'tries_remains': 2, 'word': 'm a _ a _ '}
Guessing letter: h
Sever response: {'game_id': 'b309f8eb2de2', 'status': 'ongoing', 'tries_remains': 1, 'word': 'm a _ a _ '}
G

In [8]:
#m6
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#59%


=== Game 1/100 ===
Successfully start a new game! Game ID: 06bd51adbf27. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': '06bd51adbf27', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ _ _ _ _ e _ '}
Guessing letter: s
Sever response: {'game_id': '06bd51adbf27', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ _ _ _ _ e s '}
Guessing letter: i
Sever response: {'game_id': '06bd51adbf27', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ e s '}
Guessing letter: a
Sever response: {'game_id': '06bd51adbf27', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ a _ a _ _ e s '}
Guessing letter: l
Sever response: {'game_id': '06bd51adbf27', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ a l a _ _ e s '}
Guessing letter: c
Sever response: {'game_id': '06bd51adbf27', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ a l a _ _ e s '}
Guessing letter: n
Sever response: {'game_id': '06bd51adbf27', 'status'

In [22]:
#m5
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#64%


=== Game 1/100 ===
Successfully start a new game! Game ID: e97c4d465288. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': 'e97c4d465288', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ e _ _ _ _ e _ '}
Guessing letter: r
Sever response: {'game_id': 'e97c4d465288', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ e r _ _ _ e _ '}
Guessing letter: s
Sever response: {'game_id': 'e97c4d465288', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ e r _ _ _ e _ '}
Guessing letter: d
Sever response: {'game_id': 'e97c4d465288', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ e r _ _ _ e d '}
Guessing letter: i
Sever response: {'game_id': 'e97c4d465288', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ i _ e r _ _ _ e d '}
Guessing letter: t
Sever response: {'game_id': 'e97c4d465288', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ i _ e r _ _ _ e d '}
Guessing letter: a
Sever response: {'game_id': 'e97c4d465

In [9]:
#m7
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#61%


=== Game 1/100 ===
Successfully start a new game! Game ID: c4ba9bff0e9f. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': 'c4ba9bff0e9f', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ _ _ _ _ e _ '}
Guessing letter: i
Sever response: {'game_id': 'c4ba9bff0e9f', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ e _ '}
Guessing letter: a
Sever response: {'game_id': 'c4ba9bff0e9f', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ a _ e _ '}
Guessing letter: s
Sever response: {'game_id': 'c4ba9bff0e9f', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ _ _ _ a _ e _ '}
Guessing letter: d
Sever response: {'game_id': 'c4ba9bff0e9f', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ _ _ _ a _ e d '}
Guessing letter: o
Sever response: {'game_id': 'c4ba9bff0e9f', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ o _ _ _ a _ e d '}
Guessing letter: t
Sever response: {'game_id': 'c4ba9bff0e9f', 'status'

In [348]:
#m6
N = 1000
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#59.3%


=== Game 1/1000 ===
Successfully start a new game! Game ID: 4b8fdf2d7c26. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': '4b8fdf2d7c26', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ _ '}
Guessing letter: a
Sever response: {'game_id': '4b8fdf2d7c26', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ _ _ _ _ _ _ '}
Guessing letter: i
Sever response: {'game_id': '4b8fdf2d7c26', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ _ i _ _ _ _ '}
Guessing letter: s
Sever response: {'game_id': '4b8fdf2d7c26', 'status': 'ongoing', 'tries_remains': 4, 'word': 's _ _ i _ _ _ _ '}
Guessing letter: r
Sever response: {'game_id': '4b8fdf2d7c26', 'status': 'ongoing', 'tries_remains': 3, 'word': 's _ _ i _ _ _ _ '}
Guessing letter: l
Sever response: {'game_id': '4b8fdf2d7c26', 'status': 'ongoing', 'tries_remains': 3, 'word': 's _ _ i _ _ l _ '}
Guessing letter: y
Sever response: {'game_id': '4b8fdf2d7c26', 'status': 'ongoing', 

In [346]:
#m6
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#63%


=== Game 1/100 ===
Successfully start a new game! Game ID: 3b258e7a1729. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': '3b258e7a1729', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ _ _ _ _ e '}
Guessing letter: a
Sever response: {'game_id': '3b258e7a1729', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ a _ a _ e '}
Guessing letter: t
Sever response: {'game_id': '3b258e7a1729', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ a _ a _ e '}
Guessing letter: i
Sever response: {'game_id': '3b258e7a1729', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ _ a _ a _ e '}
Guessing letter: o
Sever response: {'game_id': '3b258e7a1729', 'status': 'ongoing', 'tries_remains': 3, 'word': '_ _ _ a _ a _ e '}
Guessing letter: n
Sever response: {'game_id': '3b258e7a1729', 'status': 'ongoing', 'tries_remains': 2, 'word': '_ _ _ a _ a _ e '}
Guessing letter: u
Sever response: {'game_id': '3b258e7a1729', 'status': 'ongoing', '

In [342]:
#m5
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#61%


=== Game 1/100 ===
Successfully start a new game! Game ID: e3d112892e8c. # of tries remaining: 6. Word: _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': 'e3d112892e8c', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ '}
Guessing letter: a
Sever response: {'game_id': 'e3d112892e8c', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ _ _ _ _ _ '}
Guessing letter: s
Sever response: {'game_id': 'e3d112892e8c', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ s _ _ s s '}
Guessing letter: i
Sever response: {'game_id': 'e3d112892e8c', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ s _ i s s '}
Guessing letter: t
Sever response: {'game_id': 'e3d112892e8c', 'status': 'ongoing', 'tries_remains': 3, 'word': '_ _ s _ i s s '}
Guessing letter: p
Sever response: {'game_id': 'e3d112892e8c', 'status': 'ongoing', 'tries_remains': 2, 'word': '_ _ s _ i s s '}
Guessing letter: c
Sever response: {'game_id': 'e3d112892e8c', 'status': 'ongoing', 'tries_remains'

In [337]:
#m4
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#53%


=== Game 1/100 ===
Successfully start a new game! Game ID: 629444684860. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': '629444684860', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ _ _ _ _ e _ _ _ _ _ '}
Guessing letter: i
Sever response: {'game_id': '629444684860', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ i i _ _ e _ _ i _ _ '}
Guessing letter: n
Sever response: {'game_id': '629444684860', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ n _ i i n _ e _ n i _ _ '}
Guessing letter: a
Sever response: {'game_id': '629444684860', 'status': 'ongoing', 'tries_remains': 6, 'word': 'a n _ i i n _ e _ n i _ _ '}
Guessing letter: t
Sever response: {'game_id': '629444684860', 'status': 'ongoing', 'tries_remains': 6, 'word': 'a n t i i n _ e _ n i t _ '}
Guessing letter: y
Sever response: {'game_id': '629444684860', 'status': 'ongoing', 'tries_remains': 6, 'word': 'a n t i i n _ e _ n i t y '}
Guessing letter

In [330]:
#m3
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#46%


=== Game 1/100 ===
Successfully start a new game! Game ID: 51c299bbee11. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': '51c299bbee11', 'status': 'ongoing', 'tries_remains': 6, 'word': 'e _ _ _ _ _ _ _ _ _ _ _ '}
Guessing letter: i
Sever response: {'game_id': '51c299bbee11', 'status': 'ongoing', 'tries_remains': 5, 'word': 'e _ _ _ _ _ _ _ _ _ _ _ '}
Guessing letter: a
Sever response: {'game_id': '51c299bbee11', 'status': 'ongoing', 'tries_remains': 5, 'word': 'e _ a _ _ _ _ a _ _ _ _ '}
Guessing letter: n
Sever response: {'game_id': '51c299bbee11', 'status': 'ongoing', 'tries_remains': 4, 'word': 'e _ a _ _ _ _ a _ _ _ _ '}
Guessing letter: t
Sever response: {'game_id': '51c299bbee11', 'status': 'ongoing', 'tries_remains': 4, 'word': 'e _ a _ _ _ _ a t _ _ _ '}
Guessing letter: o
Sever response: {'game_id': '51c299bbee11', 'status': 'ongoing', 'tries_remains': 4, 'word': 'e _ a _ _ _ _ a t o _ _ '}
Guessing letter: r
Sever resp

In [327]:
#m2
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#51%


=== Game 1/100 ===
Successfully start a new game! Game ID: b02c8c4e0cb5. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': 'b02c8c4e0cb5', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ _ _ _ _ e _ '}
Guessing letter: a
Sever response: {'game_id': 'b02c8c4e0cb5', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ e _ '}
Guessing letter: i
Sever response: {'game_id': 'b02c8c4e0cb5', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ i _ _ e _ '}
Guessing letter: s
Sever response: {'game_id': 'b02c8c4e0cb5', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ i s s e s '}
Guessing letter: r
Sever response: {'game_id': 'b02c8c4e0cb5', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ _ _ i s s e s '}
Guessing letter: n
Sever response: {'game_id': 'b02c8c4e0cb5', 'status': 'ongoing', 'tries_remains': 3, 'word': '_ _ _ _ i s s e s '}
Guessing letter: u
Sever response: {'game_id': 'b02c8c4e0cb5', 'status'

In [333]:
#m1
N = 100
wins = 0

for i in range(1, N+1):
    print(f"\n=== Game {i}/{N} ===")
    try:
        # practice=1 keeps it in practice mode; verbose=True prints server messages
        ok = api.start_game(practice=1, verbose=True)
        if ok:
            wins += 1
    except Exception as e:
        print(f"[warn] Game {i} crashed with error: {e}")

print(f"\nRESULT: won {wins}/{N} games ({wins / N:.1%})")
#43%


=== Game 1/100 ===
Successfully start a new game! Game ID: fd5534b15721. # of tries remaining: 6. Word: _ _ _ _ _ _ _ _ .
Guessing letter: e
Sever response: {'game_id': 'fd5534b15721', 'status': 'ongoing', 'tries_remains': 6, 'word': '_ _ _ _ _ _ _ e '}
Guessing letter: a
Sever response: {'game_id': 'fd5534b15721', 'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ e '}
Guessing letter: i
Sever response: {'game_id': 'fd5534b15721', 'status': 'ongoing', 'tries_remains': 4, 'word': '_ _ _ _ _ _ _ e '}
Guessing letter: t
Sever response: {'game_id': 'fd5534b15721', 'status': 'ongoing', 'tries_remains': 3, 'word': '_ _ _ _ _ _ _ e '}
Guessing letter: l
Sever response: {'game_id': 'fd5534b15721', 'status': 'ongoing', 'tries_remains': 2, 'word': '_ _ _ _ _ _ _ e '}
Guessing letter: r
Sever response: {'game_id': 'fd5534b15721', 'status': 'ongoing', 'tries_remains': 1, 'word': '_ _ _ _ _ _ _ e '}
Guessing letter: o
Sever response: {'game_id': 'fd5534b15721', 'status': 'ongoing', '

## Playing recorded games:
Please finalize your code prior to running the cell below. Once this code executes once successfully your submission will be finalized. Our system will not allow you to rerun any additional games.

Please note that it is expected that after you successfully run this block of code that subsequent runs will result in the error message "Your account has been deactivated".

Once you've run this section of the code your submission is complete. Please send us your source code via email.

In [20]:
for i in range(1000):
    print('Playing ', i, ' th game')
    # Uncomment the following line to execute your final runs. Do not do this until you are satisfied with your submission
    api.start_game(practice=0,verbose=False)
    
    # DO NOT REMOVE as otherwise the server may lock you out for too high frequency of requests
    time.sleep(0.5)

Playing  0  th game
Playing  1  th game
Playing  2  th game
Playing  3  th game
Playing  4  th game
Playing  5  th game
Playing  6  th game
Playing  7  th game
Playing  8  th game
Playing  9  th game
Playing  10  th game
Playing  11  th game
Playing  12  th game
Playing  13  th game
Playing  14  th game
Playing  15  th game
Playing  16  th game
Playing  17  th game
Playing  18  th game
Playing  19  th game
Playing  20  th game
Playing  21  th game
Playing  22  th game
Playing  23  th game
Playing  24  th game
Playing  25  th game
Playing  26  th game
Playing  27  th game
Playing  28  th game
Playing  29  th game
Playing  30  th game
Playing  31  th game
Playing  32  th game
Playing  33  th game
Playing  34  th game
Playing  35  th game
Playing  36  th game
Playing  37  th game
Playing  38  th game
Playing  39  th game
Playing  40  th game
Playing  41  th game
Playing  42  th game
Playing  43  th game
Playing  44  th game
Playing  45  th game
Playing  46  th game
Playing  47  th game
Pl

HangmanAPIError: {'error': 'You have reached 1000 of games', 'status': 'denied'}

## To check your game statistics
1. Simply use "my_status" method.
2. Returns your total number of games, and number of wins.

In [21]:
[total_practice_runs,total_recorded_runs,total_recorded_successes,total_practice_successes] = api.my_status() # Get my game stats: (# of tries, # of wins)
success_rate = total_recorded_successes/total_recorded_runs
print('overall success rate = %.3f' % success_rate)

overall success rate = 0.613
